In [73]:
import requests, pandas as pd, numpy as np
from requests import session
from bs4 import BeautifulSoup

In [229]:
dfsi=pd.read_csv('dfsi.csv',sep=';')

In [230]:
dfsi2=pd.read_csv('dfsi2.csv',sep=';')

Normalize

In [231]:
dfsi.columns=['Unnamed: 0', '0', 'tavaly', 'Cégnév',
       'Alkalmazottak száma 2018', 'Alkalmazottak száma 2017',
       'Alkalmazottak száma 2016','Alkalmazottak száma 2015', 'region', 'nr', 'coords', 'kws', 'cms']
dfsi2.columns=['Unnamed: 0', '0', 'tavaly', 'Cégnév',
       'Árbevétel 2018 (RON)', 'Árbevétel 2017 (RON)', 'Árbevétel 2016 (RON)','Árbevétel 2015 (RON)',
       'region', 'nr', 'coords', 'kws', 'cms']

In [232]:
dfsi['nr_alkalmazottak']=dfsi['nr']
dfsi2['nr_arbevetel']=dfsi2['nr']

In [233]:
dfsi.head(2)

Unnamed: 0  0 tavaly                                Cégnév  \
0           0  1      2  READY GARMENT TECHNOLOGY ROMANIA SRL   
1           1  2      1                            VALKES SRL   

  Alkalmazottak száma 2018 Alkalmazottak száma 2017 Alkalmazottak száma 2016  \
0                      990                      730                    1 005   
1                      621                      788                      886   

  Alkalmazottak száma 2015          region  nr                         coords  \
0                    1 199  also-haromszek   1  ['45.8772830', ' 25.7994510']   
1                    1 007  also-haromszek   2  ['45.855129 ', ' 25.806651 ']   

                            kws  \
0  ['mosas-tisztitas', '', '"']   
1          ['kabelek', '', '"']   

                                                 cms  nr_alkalmazottak  
0  520036, Sepsiszentgy\xf6rgy, Cs\xedki u., 149/A\t                 1  
1  520077, Sepsiszentgy\xf6rgy, P&#259;i&#351; Da...                 2

In [234]:
dfsi2.head(2)

Unnamed: 0  0 tavaly                      Cégnév Árbevétel 2018 (RON)  \
0           0  1      1  FABRICA DE LAPTE BRASOV SA          468 016 207   
1           1  2      2                 COVALACT SA          252 640 519   

  Árbevétel 2017 (RON) Árbevétel 2016 (RON) Árbevétel 2015 (RON)  \
0          431 950 759          370 418 528          338 283 110   
1          235 415 329          230 073 646          199 493 229   

           region  nr                         coords  \
0  also-haromszek   1  ['46.0750630', ' 25.6087250']   
1  also-haromszek   2  ['45.869573 ', ' 25.800705 ']   

                           kws  \
0  ['tejfeldolgozas', '', '"']   
1  ['tejfeldolgozas', '', '"']   

                                               cms  nr_arbevetel  
0               525100, Bar\xf3t, V\xedz u., 109\t             1  
1  520036, Sepsiszentgy\xf6rgy, Oltmez\xf5 u., 1\t             2

In [235]:
data=dfsi.set_index('Cégnév').join(dfsi2.set_index('Cégnév'),how='outer',lsuffix='_left', rsuffix='_right')

In [236]:
data['Cím']=data[['cms_right','cms_left']].T.ffill().bfill().T['cms_right']
data['Koord']=data[['coords_right','coords_left']].T.ffill().bfill().T['coords_right']
data['Kw']=data[['kws_right','kws_left']].T.ffill().bfill().T['kws_right']
data['Régió']=data[['region_right','region_left']].T.ffill().bfill().T['region_right']

In [237]:
data=data.drop(['0_left', 'region_left','nr_left', 'coords_left', 'kws_left', 'cms_left',
       '0_right', 'region_right', 'nr_right', 'coords_right', 'kws_right', 'cms_right',
        'Unnamed: 0_left','Unnamed: 0_right'],axis=1).reset_index()

In [238]:
data.head()

Cégnév tavaly_left Alkalmazottak száma 2018  \
0             A M C SRL         NaN                      NaN   
1         ABC IMPEX SRL          20                      139   
2           ABRAZIV SRL         NaN                      NaN   
3      ADILEX FUNGO SRL         NaN                      NaN   
4  ADIMAG COM IMPEX SRL         NaN                      NaN   

  Alkalmazottak száma 2017 Alkalmazottak száma 2016 Alkalmazottak száma 2015  \
0                      NaN                      NaN                      NaN   
1                      145                      132                      132   
2                      NaN                      NaN                      NaN   
3                      NaN                      NaN                      NaN   
4                      NaN                      NaN                      NaN   

   nr_alkalmazottak tavaly_right Árbevétel 2018 (RON) Árbevétel 2017 (RON)  \
0               NaN           20           28 716 061           27 881 270   
1              21.0           20           37 875 372           36 539 530   
2               NaN           49           16 316 705            5 483 275   
3               NaN          >50            6 834 996              925 866   
4               NaN           36           65 548 663           57 106 224   

  Árbevétel 2016 (RON) Árbevétel 2015 (RON)  nr_arbevetel  \
0           24 390 005           22 173 039          22.0   
1           33 071 733           31 956 498          24.0   
2                    0                    0          17.0   
3                    -                    -          50.0   
4           48 827 471           47 437 389          40.0   

                                                 Cím  \
0           527100, H\xeddv\xe9g, Rom\xe1n u., 203\t   
1  535600, Sz\xe9kelyudvarhely, R\xe1k\xf3czi Fer...   
2  535500, Gyergy\xf3szentmikl\xf3s, \xc1llom\xe1...   
3                          537355, Vasl\xe1b, , 37\t   
4  540190, Marosv\xe1s\xe1rhely, Szabads\xe1g u.,...   

                           Koord  \
0  ['45.8391350', ' 25.5892160']   
1  ['46.289768 ', ' 25.290034 ']   
2  ['46.7174250', ' 25.5751650']   
3      ['46.64607', ' 25.62371']   
4    ['46.537905', ' 24.548819']   

                                                  Kw           Régió  
0                      ['nagykereskedelem', '', '"']  also-haromszek  
1           ['csomagoloanyagok', 'nyomdak', '', '"']   udvarhelyszek  
2                         ['szerszamgepek', '', '"']     gyergyoszek  
3           ['zoldseg-gyumolcs-csomagolas', '', '"']     gyergyoszek  
4  ['belsoepiteszeti-anyagok', 'epitoanyagok', 'f...       marosszek

In [239]:
lat=[]
lon=[]
for i in range(len(data.index)):
    k=data.loc[data.index[i]]['Koord'].replace("'",'').replace('[','')\
    .replace(']','').replace(' ','').split(',')
    lon.append(k[0])
    lat.append(k[1])

In [240]:
data['Latitude']=lat
data['Longitude']=lon

In [241]:
data=data.drop('Koord',axis=1)

In [242]:
data

Cégnév tavaly_left Alkalmazottak száma 2018  \
0               A M C SRL         NaN                      NaN   
1           ABC IMPEX SRL          20                      139   
2             ABRAZIV SRL         NaN                      NaN   
3        ADILEX FUNGO SRL         NaN                      NaN   
4    ADIMAG COM IMPEX SRL         NaN                      NaN   
..                    ...         ...                      ...   
419        WONDERLAND SRL          44                       28   
420     ZABOLA ESTATE SRL          39                       45   
421    ZAMBELLI METAL SRL          15                      205   
422       ZARAH MODEN SRL           2                      764   
423       ZENCO TRANS SRL          40                       36   

    Alkalmazottak száma 2017 Alkalmazottak száma 2016  \
0                        NaN                      NaN   
1                        145                      132   
2                        NaN                      NaN   
3                        NaN                      NaN   
4                        NaN                      NaN   
..                       ...                      ...   
419                       29                       28   
420                       31                       25   
421                      179                      162   
422                      785                      778   
423                       37                       33   

    Alkalmazottak száma 2015  nr_alkalmazottak tavaly_right  \
0                        NaN               NaN           20   
1                        132              21.0           20   
2                        NaN               NaN           49   
3                        NaN               NaN          >50   
4                        NaN               NaN           36   
..                       ...               ...          ...   
419                       29              46.0          NaN   
420                       23              28.0          NaN   
421                      163              14.0           15   
422                      839               2.0            2   
423                       33              41.0          NaN   

    Árbevétel 2018 (RON) Árbevétel 2017 (RON) Árbevétel 2016 (RON)  \
0             28 716 061           27 881 270           24 390 005   
1             37 875 372           36 539 530           33 071 733   
2             16 316 705            5 483 275                    0   
3              6 834 996              925 866                    -   
4             65 548 663           57 106 224           48 827 471   
..                   ...                  ...                  ...   
419                  NaN                  NaN                  NaN   
420                  NaN                  NaN                  NaN   
421           52 694 046           42 016 920           34 591 562   
422          154 604 899          148 531 005          141 121 629   
423                  NaN                  NaN                  NaN   

    Árbevétel 2015 (RON)  nr_arbevetel  \
0             22 173 039          22.0   
1             31 956 498          24.0   
2                      0          17.0   
3                      -          50.0   
4             47 437 389          40.0   
..                   ...           ...   
419                  NaN           NaN   
420                  NaN           NaN   
421           27 891 895          15.0   
422          139 752 712           2.0   
423                  NaN           NaN   

                                                   Cím  \
0             527100, H\xeddv\xe9g, Rom\xe1n u., 203\t   
1    535600, Sz\xe9kelyudvarhely, R\xe1k\xf3czi Fer...   
2    535500, Gyergy\xf3szentmikl\xf3s, \xc1llom\xe1...   
3                            537355, Vasl\xe1b, , 37\t   
4    540190, Marosv\xe1s\xe1rhely, Szabads\xe1g u.,...   
..                                                 ...   
419                     527160, 

In [243]:
manual=data[data['Longitude']=='']
data=data[data['Longitude']!='']

In [222]:
data.to_excel('data.xlsx')
manual.to_excel('manual.xlsx')
manual.to_excel('manual_manual.xlsx')

Fix sector, address data and coordinates manually

In [244]:
manual=pd.read_excel('manual_manual.xlsx')

In [245]:
data=pd.concat([data,manual]).set_index('Cégnév')

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [246]:
sectors=pd.read_excel('sectors.xlsx')
sectormap={}
repl={'á':'a','é':'e','í':'i','ó':'o','ú':'u','ü':'u','ű':'u','ő':'o','ö':'o'}
for s in sectors.columns:
    for k in sectors[s].values:
        for j in str(k).replace(' ','').split(','):
            sectormap[j]=s
            for c in repl:
                j=j.replace(c,repl[c])
            sectormap[j]=s

In [247]:
valid=[]
kws=[]
ki=-1
for i in range(len(data.index)):
    ks=data.loc[data.index[i]]['Kw'].replace("'",'').replace('[','')\
                .replace(']','').replace(' ','').lower().split(',')[:-2]
    for k in ks:
        if k in sectormap:
            kws.append(sectormap[k])
            break
        k=k.replace('-','')
        if k in sectormap:
            kws.append(sectormap[k])
            break
    if len(kws)<i-1: 
        print('ERROR',ks,i)
        break
    else:
        #print('SUCCES',kws[-1],ks)
        valid.append([data.index[i],kws[-1],ks])

In [248]:
pd.DataFrame(valid).to_excel('valid.xlsx')
pd.DataFrame(valid).to_excel('valid_manual.xlsx')

Manual overwrite